In [1]:
!pip install -U adapter-transformers datasets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.4/6.4 MB 51.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 469.0/469.0 KB 42.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.2/199.2 KB 24.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 100.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 73.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 KB 28.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 KB 18.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 KB 16.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 KB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 KB 19.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.6/264.6 KB 32.3 MB/s eta 0:00:00
     ━━━━━━━━━━

In [2]:
from datasets import load_dataset
dataset = load_dataset("amazon_polarity")
dataset.num_rows


Generating train split:   0%|          | 0/3600000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/400000 [00:00<?, ? examples/s]

Dataset amazon_polarity downloaded and prepared to /root/.cache/huggingface/datasets/amazon_polarity/amazon_polarity/3.0.0/a27b32b7e7b88eb274a8fa8ba0f654f1fe998a87c22547557317793b5d2772dc. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

{'train': 3600000, 'test': 400000}

In [3]:
dataset

DatasetDict({
    train: Dataset({
        features: ['label', 'title', 'content'],
        num_rows: 3600000
    })
    test: Dataset({
        features: ['label', 'title', 'content'],
        num_rows: 400000
    })
})

In [4]:
dataset.num_rows

{'train': 3600000, 'test': 400000}

In [5]:
dataset["train"][0]

{'label': 1,
 'title': 'Stuning even for the non-gamer',
 'content': 'This sound track was beautiful! It paints the senery in your mind so well I would recomend it even to people who hate vid. game music! I have played the game Chrono Cross but out of all of the games I have ever played it has the best music! It backs away from crude keyboarding and takes a fresher step with grate guitars and soulful orchestras. It would impress anyone who cares to listen! ^_^'}

In [6]:
dataset["test"][0]

{'label': 1,
 'title': 'Great CD',
 'content': 'My lovely Pat has one of the GREAT voices of her generation. I have listened to this CD for YEARS and I still LOVE IT. When I\'m in a good mood it makes me feel better. A bad mood just evaporates like sugar in the rain. This CD just oozes LIFE. Vocals are jusat STUUNNING and lyrics just kill. One of life\'s hidden gems. This is a desert isle CD in my book. Why she never made it big is just beyond me. Everytime I play this, no matter black, white, young, old, male, female EVERYBODY says one thing "Who was that singing ?"'}

In [7]:
dataset = dataset.remove_columns("title")

In [8]:
dataset

DatasetDict({
    train: Dataset({
        features: ['label', 'content'],
        num_rows: 3600000
    })
    test: Dataset({
        features: ['label', 'content'],
        num_rows: 400000
    })
})

In [9]:
from transformers import AutoTokenizer, RobertaTokenizer

tokenizer = RobertaTokenizer.from_pretrained("roberta-base")

In [10]:
def encode_batch(batch):
  return tokenizer(batch["content"], max_length=100, truncation = True, padding="max_length")

In [11]:
dataset = dataset.map(encode_batch, batched=True)

Map:   0%|          | 0/3600000 [00:00<?, ? examples/s]

Map:   0%|          | 0/400000 [00:00<?, ? examples/s]

In [12]:
dataset = dataset.rename_column("label", "labels")

In [13]:
dataset.set_format(type="torch", columns=["input_ids", "attention_mask", "labels"])

In [14]:
from transformers import RobertaConfig, RobertaModelWithHeads
model = RobertaModelWithHeads.from_pretrained("roberta-base")

/usr/local/lib/python3.9/dist-packages/transformers/adapters/models/roberta/adapter_model.py:274: FutureWarning: This class has been renamed to `RobertaAdapterModel` in v3. Please use the new class instead as this class might be removed in a future version.
  warnings.warn(


/usr/local/lib/python3.9/dist-packages/transformers/adapters/models/roberta/adapter_model.py:252: FutureWarning: This class has been renamed to `RobertaAdapterModel` in v3. Please use the new class instead as this class might be removed in a future version.
  warnings.warn(
Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModelWithHeads: ['lm_head.bias', 'lm_head.dense.bias', 'lm_head.layer_norm.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight']
- This IS expected if you are initializing RobertaModelWithHeads from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModelWithHeads from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification mod

In [15]:
model.add_adapter("amazon_polarity")
# Add a matching classification head
model.add_classification_head(
    "amazon_polarity",
    num_labels=2,
    id2label={ 0: "negative", 1: "positive"}
  )
# Activate the adapter
model.train_adapter("amazon_polarity")

In [41]:
import numpy as np
from transformers import TrainingArguments, AdapterTrainer, EvalPrediction

training_args = TrainingArguments(
    learning_rate=3e-4,
    max_steps=80000,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=32,
    logging_steps=1000,
    output_dir="adapter-roberta-base-amazon-polarity",
    overwrite_output_dir=True,
    # The next line is important to ensure the dataset labels are properly passed to the model
    remove_unused_columns=False,
)

def compute_accuracy(eval_pred):
  preds = np.argmax(eval_pred.predictions, axis=1)
  return {"acc": (preds == eval_pred.label_ids).mean()}

trainer = AdapterTrainer(
    model=model,
    args=training_args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    compute_metrics=compute_accuracy,
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
max_steps is given, it will override any value given in num_train_epochs


In [18]:
trainer.train()

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 3600000
  Num Epochs = 1
  Instantaneous batch size per device = 32
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 1
  Total optimization steps = 80000
  Number of trainable parameters = 1486658


Saving model checkpoint to ./training_output/checkpoint-500
Configuration saved in ./training_output/checkpoint-500/amazon_polarity/adapter_config.json
Module weights saved in ./training_output/checkpoint-500/amazon_polarity/pytorch_adapter.bin
Configuration saved in ./training_output/checkpoint-500/amazon_polarity/head_config.json
Module weights saved in ./training_output/checkpoint-500/amazon_polarity/pytorch_model_head.bin
Configuration saved in ./training_output/checkpoint-500/amazon_polarity/head_config.json
Module weights saved in ./training_output/checkpoint-500/amazon_polarity/pytorch_model_head.bin
Saving model checkpoint to ./training_output/checkpoint-1000
Configuration saved in ./training_output/checkpoint-1000/amazon_polarity/adapter_config.json
Module weights saved in ./training_output/checkpoint-1000/amazon_polarity/pytorch_adapter.bin
Configuration saved in ./training_output/checkpoint-1000/amazon_polarity/head_config.json
Module weights saved in ./training_output/check

TrainOutput(global_step=80000, training_loss=0.13133217878341674, metrics={'train_runtime': 7884.1676, 'train_samples_per_second': 324.701, 'train_steps_per_second': 10.147, 'total_flos': 1.33836672e+17, 'train_loss': 0.13133217878341674, 'epoch': 0.71})

In [19]:
trainer.evaluate()

***** Running Evaluation *****
  Num examples = 400000
  Batch size = 32


{'eval_loss': 0.1150890588760376,
 'eval_acc': 0.95941,
 'eval_runtime': 559.0469,
 'eval_samples_per_second': 715.503,
 'eval_steps_per_second': 22.359,
 'epoch': 0.71}

In [20]:
from transformers import TextClassificationPipeline

classifier = TextClassificationPipeline(model=model, tokenizer=tokenizer, device=training_args.device.index)

classifier("I came across a lot of reviews stating that it is the best book out there.")

The model 'RobertaModelWithHeads' is not supported for . Supported models are ['AlbertForSequenceClassification', 'BartForSequenceClassification', 'BertForSequenceClassification', 'BigBirdForSequenceClassification', 'BigBirdPegasusForSequenceClassification', 'BloomForSequenceClassification', 'CamembertForSequenceClassification', 'CanineForSequenceClassification', 'ConvBertForSequenceClassification', 'CTRLForSequenceClassification', 'Data2VecTextForSequenceClassification', 'DebertaForSequenceClassification', 'DebertaV2ForSequenceClassification', 'DistilBertForSequenceClassification', 'ElectraForSequenceClassification', 'ErnieForSequenceClassification', 'EsmForSequenceClassification', 'FlaubertForSequenceClassification', 'FNetForSequenceClassification', 'FunnelForSequenceClassification', 'GPT2ForSequenceClassification', 'GPT2ForSequenceClassification', 'GPTNeoForSequenceClassification', 'GPTJForSequenceClassification', 'IBertForSequenceClassification', 'LayoutLMForSequenceClassification'

[{'label': 'positive', 'score': 0.5589291453361511}]

In [21]:
model.save_adapter("./final_adapter", "amazon_polarity")



Configuration saved in ./final_adapter/adapter_config.json
Module weights saved in ./final_adapter/pytorch_adapter.bin
Configuration saved in ./final_adapter/head_config.json
Module weights saved in ./final_adapter/pytorch_model_head.bin


In [22]:
!ls -lh final_adapter

total 5.7M
-rw-r--r-- 1 root root 1.1K Mar 12 19:38 adapter_config.json
-rw-r--r-- 1 root root  411 Mar 12 19:38 head_config.json
-rw-r--r-- 1 root root 3.5M Mar 12 19:38 pytorch_adapter.bin
-rw-r--r-- 1 root root 2.3M Mar 12 19:38 pytorch_model_head.bin


In [25]:
from huggingface_hub import notebook_login
notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [26]:
model.push_to_hub("my-awesome-model")

Configuration saved in /tmp/tmp2jblmuy6/config.json
Configuration saved in /tmp/tmp2jblmuy6/generation_config.json
Model weights saved in /tmp/tmp2jblmuy6/pytorch_model.bin
Uploading the following files to DrishtiSharma/my-awesome-model: generation_config.json,pytorch_model.bin,config.json


Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

pytorch_model.bin:   0%|          | 0.00/505M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/DrishtiSharma/my-awesome-model/commit/4016b0f4e89c856fac3b2b624681e2949a1557aa', commit_message='Upload model', commit_description='', oid='4016b0f4e89c856fac3b2b624681e2949a1557aa', pr_url=None, pr_revision=None, pr_num=None)

In [30]:
!pip install pickle5

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.1/132.1 KB 4.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pickle5: filename=pickle5-0.0.11-cp39-cp39-linux_x86_64.whl size=255897 sha256=448f06eb1826fdb1f14b27a0232477f9cfb2e76ca6e385db52464b4deedff020
  Stored in directory: /root/.cache/pip/wheels/f2/7a/49/9bef8878949914ecb90c08fc5bf30a05e17f475fe7e08b63a8
Successfully built pickle5


In [31]:
from huggingface_hub import HfApi, snapshot_download

from huggingface_hub.repocard import metadata_eval_result, metadata_save

from pathlib import Path
import pickle5 as pickle
import datetime
import json

In [43]:
def push_to_hub(repo_id, model, local_repo_path="hub"):
    """
    Evaluate, Generate a video and Upload a model to Hugging Face Hub.
    This method does the complete pipeline:
    - It evaluates the model
    - It generates the model card
    - It generates a replay video of the agent
    - It pushes everything to the Hub

    :param repo_id: repo_id: id of the model repository from the Hugging Face Hub
    :param env
    :param video_fps: how many frame per seconds to record our video replay
    (with taxi-v3 and frozenlake-v1 we use 1)
    :param local_repo_path: where the local repository is
    """
    _, repo_name = repo_id.split("/")

    api = HfApi()

    # Step 1: Create the repo
    repo_url = api.create_repo(
        repo_id=repo_id,
        exist_ok=True,
    )

    # Step 2: Download files
    repo_local_path = Path(snapshot_download(repo_id=repo_id))


    # Pickle the model
    with open((repo_local_path) / "adapter-roberta-base-amazon-polarity.pkl", "wb") as f:
        pickle.dump(model, f)


    evaluate_data = {
        "eval_loss": 0.1150890588760376,
        'eval_acc': 0.95941,
        'eval_samples_per_second': 715.503,
        'eval_steps_per_second': 22.359,
        'eval_steps_per_second': 22.359,
        'epoch': 0.71,
        "eval_datetime": datetime.datetime.now().isoformat(),
    }


    # Write a JSON file called "results.json" that will contain the
    # evaluation results
    with open(repo_local_path / "results.json", "w") as outfile:
        json.dump(evaluate_data, outfile)



    metadata = {}
    metadata["tags"] = ["text-classification", "amazon-polarity", "roberta-base", "Adapter"]


    # Merges both dictionaries
    metadata = {**metadata}

    model_card = f"""
    # **we train an adapter for a RoBERTa model for sequence classification on a sentiment analysis task using adapter-transformers, the AdapterHub adaptation of HuggingFace's transformers library.**

    ## Usage

    ```python

    model = load_from_hub(repo_id="{repo_id}", filename="adapter-roberta-base-amazon-polarity.pkl")

    ```
    """



    readme_path = repo_local_path / "README.md"
    readme = ""
    print(readme_path.exists())
    if readme_path.exists():
        with readme_path.open("r", encoding="utf8") as f:
            readme = f.read()
    else:
        readme = model_card

    with readme_path.open("w", encoding="utf-8") as f:
        f.write(readme)

    # Save our metrics to Readme metadata
    metadata_save(readme_path, metadata)


    # Step 7. Push everything to the Hub
    api.upload_folder(
        repo_id=repo_id,
        folder_path=repo_local_path,
        path_in_repo=".",
    )

    print("Your model is pushed to the Hub. You can view your model here: ", repo_url)

In [44]:
username = "DrishtiSharma"  # FILL THIS
repo_name = "Adapter-for-RoBERTa-on-amazon-polarity"
push_to_hub(repo_id=f"{username}/{repo_name}", model=model)

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

True
Your model is pushed to the Hub. You can view your model here:  https://huggingface.co/DrishtiSharma/Adapter-for-RoBERTa-on-amazon-polarity


In [37]:
!apt install git-lfs

Reading package lists... Done
Building dependency tree       
Reading state information... Done
git-lfs is already the newest version (2.9.2-1).
0 upgraded, 0 newly installed, 0 to remove and 22 not upgraded.


In [38]:
!git config --global credential.helper store

In [45]:
trainer.push_to_hub()

Saving model checkpoint to adapter-roberta-base-amazon-polarity
Configuration saved in adapter-roberta-base-amazon-polarity/amazon_polarity/adapter_config.json
Module weights saved in adapter-roberta-base-amazon-polarity/amazon_polarity/pytorch_adapter.bin
Configuration saved in adapter-roberta-base-amazon-polarity/amazon_polarity/head_config.json
Module weights saved in adapter-roberta-base-amazon-polarity/amazon_polarity/pytorch_model_head.bin
Configuration saved in adapter-roberta-base-amazon-polarity/amazon_polarity/head_config.json
Module weights saved in adapter-roberta-base-amazon-polarity/amazon_polarity/pytorch_model_head.bin
Dropping the following result as it does not have all the necessary fields:
{'dataset': {'name': 'amazon_polarity', 'type': 'amazon_polarity', 'config': 'amazon_polarity', 'split': 'test', 'args': 'amazon_polarity'}}
